# PROJET ST7  KARHOO

In [73]:
# Modules de base
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

# Module relatif à Gurobi
from gurobipy import *
import gurobipy as grb
from gurobipy import GRB

In [74]:
import json
import csv
import numpy as np
import pandas as pd

# Opening JSON file
f = open('day_data.json')
 
# returns JSON object as
# a dictionary
data = json.load(f)
 
# Iterating through the json
# list
 
# Closing file
f.close()


time = pd.read_csv('travel_times.csv',sep=';',index_col=0)

### Définition du modèle et des données

Notre modèle est composé de 4 ensembles : P, D, N et K.
<ul>
    <li>P correspond à l'ensemble des stations de pick-up des courses.</li>
    <li>D correspond à l'ensemble des stations de drop-off des courses.</li>
    <li>N correspond à $P\cup D \cup \{0,2n+1\}$
    <li>K correspond à l'ensemble des chauffeurs</li>
</ul>

In [75]:
M = Model("Projet Karhoo")

m = 8 # nombre de chauffeurs/véhicules
n = len(data["bookings"]) # nombre de courses

N = []
N.append('s0')
for elt in data["bookings"]: #Ensemble des stations de départ P et d'arrivée D
    N.append(elt["jobs"][0]["station"])
for elt in data["bookings"]:
    N.append(elt["jobs"][1]["station"])
N.append('s0')

courses = []
for elt in data["bookings"]:
    courses.append(elt)
    
chauffeurs = []
for elt in data["shifts"]:
    chauffeurs.append(elt)

### Définition des variables

<font><div align="center">Tableau regroupant les variables utilisées dans le modèle</div></font>

| Nom Variable 	| Type (entier, binaire, continue) 	| Description 	|
|:------------:	|:--------------------------------:	|:-----------:	|
|  X<sub>k,i,j  	|            binaire            	|  Le chauffeur k fait le trajet entre la station i et la station j dans la liste des stations desservies pour les courses 	|
|  B<sub>k,i  	|            entier            	|  Date de prise/dépôt du passager de la course i par le chauffeur k   	|
|  L<sub>k,i  	|            binaire            	|  Temps de trajet du passager de la course i par le chauffeur k 	|
|  Q<sub>k,i  	|            binaire            	|  Capacité de la voiture du chauffeur k après avoir récupéré les passagers de la course i	|


<font><div>pour tout i,j entier entre 0 et 51 et k entier entre 1 et 8
    
Les i,j correspondent aux stations de départ et d'arrivée des courses dans notre liste pour le datasheet importé.</div></font>

In [76]:
# Création des variables
X = M.addVars([(k,i,j) for k in range(1,m+1) for i in range(len(N)) for j in range(len(N))],vtype = GRB.BINARY, name = "X")
B = M.addVars([(k,i) for k in range(1,m+1) for i in range(len(N))],vtype = GRB.INTEGER, name = "date")
L = M.addVars([(k,i) for k in range(1,m+1) for i in range(1,n+1)], vtype= GRB.INTEGER, name = "L")
Q = M.addVars([(k,i) for k in range(1,m+1) for i in range(len(N))], vtype= GRB.INTEGER, name = "Q")

### Définition des contraintes

#### Une course a au plus un chauffeur
$$\sum_{k \in K}\sum_{j \in N} x_{k,i,j} \leq 1 \;\;\;\; \forall i \in P \;\;\;$$

In [77]:
# Une course a un chauffeur unique
for i in range(1,len(N)//2): # somme sur les courses
    M.addLConstr(grb.quicksum([X[k,i,j] for k in range(1,m+1) for j in range(len(N))]), sense = "<=", rhs = 1)

#### Chaque chauffeur commence au dépôt
$$\sum_{j \in P\cup D} x_{k,0,j} = 1 \;\;\;\; \forall k \in K \;\;\;$$

In [78]:
# Chaque chauffeur commence au dépôt
for k in range(1,m+1):
    M.addConstr(grb.quicksum([X[k,0,j] for j in range(1,len(N)-1)]) == 1)

#### Chaque chauffeur finit au dépôt
$$\sum_{i \in P\cup D} x_{k,i,(2n+1)} = 1 \;\;\;\; \forall k \in K \;\;\;$$

In [79]:
# Chaque chauffeur finit au dépôt
for k in range(1,m+1):
    M.addConstr(grb.quicksum([X[k,i,len(N)-1] for i in range(1,len(N)-1)]) == 1)

#### Continuité
$$\sum_{j \in N} x_{k,i,j} - \sum_{j \in N} x_{k,j,i}  = 0 \;\;\;\; \forall k \in K \;\; \forall i \in P\cup D \;\;\;$$

In [80]:
# Continuité
for k in range(1,m+1):
    for i in range(1,len(N)-1):
        M.addConstr(grb.quicksum([X[k,i,j]-X[k,j,i] for j in range(len(N))]) == 0)

#### Un passager ne reste pas plus que le temps fixé dans la voiture du chauffeur
$$ L_{k,i} = B_{k,n+i} - B_{k,i} - d_i \;\;\;\; \forall i \in P \;\; \forall k \in K \;\;\;$$
$$ L_{k,i} \geq t_{i,n+i} \;\;\;\; \forall i \in P \;\; \forall k \in K \;\;\;$$
$$ L_{k,i} \leq T_{i} \;\;\;\; \forall i \in P \;\; \forall k \in K \;\;\;$$

In [81]:
# Un passager ne reste pas plus longtemps qu'un temps fixe mi dans la voiture
for k in range(1,m+1):
    for i in range(1,len(N)//2):
        M.addConstr(L[k,i] == B[k,n+i] - B[k,i] - courses[i-1]["jobs"][0]["duration"])
        M.addConstr(L[k,i] >= time[N[i+n]][N[i]])
        M.addConstr(L[k,i] <= courses[i-1]["maximumDuration"])

#### Le revenu maximal du chauffeur n'est pas dépassé
$$ \sum_{i \in P}\sum_{j \in N} x_{k,i,j} p_{i} \leq r_{k}  \;\;\;\; \forall k \in K \;\;\;$$ $$\text{avec $p_i$ prix de la course i et $r_k$ revenu maximal du chauffeur k}$$

In [82]:
# On ne dépasse pas le revenu maximal du chauffeur
for k in range(1,m+1):
    M.addConstr(quicksum([X[k,i,j]*courses[i-1]["price"] for i in range (1,len(N)//2) for j in range(len(N))]) <= chauffeurs[k-1]["maximumTurnover"])

#### Début et fin de service
$$ B_{k,0} \geq L_{k}  \;\;\;\; \forall k \in K \;\;\;$$
$$ B_{k,2n+1} \leq U_{k}  \;\;\;\; \forall k \in K \;\;\;$$

In [83]:
# Début et fin de service
for k in range(1,m+1):
    M.addConstr(B[k,0] >= chauffeurs[k-1]["jobs"][0]["timeDate"])
    M.addConstr(B[k,len(N)-1] <= chauffeurs[k-1]["jobs"][1]["timeDate"])

#### Le chauffeur arrive dans la fenêtre de temps définie pour la course
$$ \forall k \in K \; et \; \forall i \in P \;\; \left\{ 
    \begin{array}{ll} 
        B_{k,i} \geq l_{i} \\
        B_{k,i} \leq u_{i}  \\
        B_{k,n+i} \geq l_{n+i} \\
        B_{k,n+i} \leq u_{n+i}
      \end{array}
     \right.
$$

In [84]:
# Le chauffeur arrive dans la fenêtre de temps
for k in range(1,m+1):
    for i in range(1,len(N)//2):
        M.addConstr(courses[i-1]["jobs"][0]["timeWindowBeginDate"]<=B[k,i])
        M.addConstr(courses[i-1]["jobs"][0]["timeWindowEndDate"]>=B[k,i])
        M.addConstr(courses[i-1]["jobs"][1]["timeWindowBeginDate"]<=B[k,n+i])
        M.addConstr(courses[i-1]["jobs"][1]["timeWindowEndDate"]>=B[k,n+i])

#### Capacité du véhicule après passage au noeud i
$$\\max{(0, q_{i})} ≤  Q_{i,k} ≤ \min{(Q_{k}, Q_{k} + q_{i})} )\;\;\;\; \forall i \in P\cup D, \;  k \in K \;\;\;$$

$$\ Q_{j,k}  ≥ Q_{i,k} + q_{j}- Q_{k}(1-x_{i,j,k})\;\;\;\; \forall i \in P\cup D, \; j \in P\cup D,\; k \in K \;\;\;$$


In [85]:
# Capacité après un noeud i
for k in range(1,m+1):
    for i in range(1,len(N)//2):
        M.addConstr(Q[k,i] >= courses[i-1]["passengers"])
        M.addConstr(Q[k,i] <= chauffeurs[k-1]["capacity"])
    for i in range(len(N)//2, len(N)-1):
        M.addConstr(Q[k,i] >= 0)
        M.addConstr(Q[k,i] <= chauffeurs[k-1]["capacity"]-courses[i-1-len(N)//2-1]["passengers"])
        
for k in range(1,m+1):
    for j in range(1,len(N)//2):
        for i in range(1,len(N)-1):
            M.addConstr(Q[k,j] >= Q[k,i] +courses[j-1]["passengers"]-chauffeurs[k-1]["capacity"]*(1-X[k,i,j]))
    for j in range(len(N)//2,len(N)-1):
        for i in range(1,len(N)-1):
            M.addConstr(Q[k,j] >= Q[k,i] -courses[j-1-len(N)//2-1]["passengers"]-chauffeurs[k-1]["capacity"]*(1-X[k,i,j]))

#### Le chauffeur qui prend un passager est celui que le dépose
$$\ \sum_{j \in N}  x_{i,j} -  \sum_{j \in N}  x_{n+i j} = 0\;\;\;\; \forall i \in P, \; k \in K \;\;\;$$

In [86]:
# Le chauffeur qui prend un passager est celui qui le dépose
for k in range(1,m+1):
    for i in range(1,len(N)//2):
        M.addConstr(quicksum([X[k,i,j] - X[k,n+i,j] for j in range(len(N))])==0)

#### Contrainte sur la date de prise/dépôt
$$\ B_{j,k}  ≥ B_{i,k} + d_{i} +t_{i,j} - 604799(1-x_{i,j,k})\;\;\;\; \forall i \in N, \; j \in N,\; k \in K \;\;\;$$
$$\ avec \; l_{i} + d_{i} + t_{ij} - e_{j} = 604799  $$

In [87]:
# Contrainte sur la date de dépot/prise
for k in range(1,m+1):
    for i in range(len(N)):
        for j in range(len(N)):
            if i == 0 or i == len(N)-1:
                M.addConstr(B[k,j] >= B[k,i] + time[N[j]][N[i]] - 604799*(1-X[k,i,j]))
            else:    
                M.addConstr(B[k,j] >= B[k,i] + 60 + time[N[j]][N[i]] - 604799*(1-X[k,i,j]))
# Contrainte sur la date de dépot/prise
for k in range(1,m+1):
    for i in range(1,len(N)//2):
        M.addConstr(B[k,i+n] >= B[k,i] + 60 + time[N[i+n]][N[i]])

<p style="text-align: center;font-size: 15pt;"><b> Fonction Objectif</p>

$$Maximize \sum_{k \in K}\sum_{i \in P}\sum_{j \in N} x_{k,i,j} \;\;\;\; $$

In [88]:
# Fonction objectif
M.setObjective(quicksum([X[k,i,j] for i in range(1,len(N)//2) for j in range(len(N)) for k in range(1,m+1)]),GRB.MAXIMIZE)
M.update()

In [89]:
M.optimize()

Gurobi Optimizer version 9.5.0 build v9.5.0rc5 (win64)
Thread count: 8 physical cores, 16 logical processors, using up to 16 threads
Optimize a model with 44697 rows, 22664 columns and 209480 nonzeros
Model fingerprint: 0x3ca009a0
Variable types: 0 continuous, 22664 integer (21632 binary)
Coefficient statistics:
  Matrix range     [1e+00, 6e+05]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 6e+05]
Presolve removed 35935 rows and 14425 columns
Presolve time: 2.38s
Presolved: 8762 rows, 8239 columns, 52098 nonzeros
Variable types: 0 continuous, 8239 integer (7454 binary)

Root relaxation: objective 2.500000e+01, 3594 iterations, 0.57 seconds (0.22 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0   25.00000    0  357          -   25.00000      -     -    6s
     0     0   25.00000    0  302          -   25.00000   

### Affichage de la solution

In [90]:
# Affichage de la solution
def takeThird(L):
    return L[2]

res = 0
attrib = []
print("Attribution des courses :")
for k in range(1,m+1):
    chauffeur = []
    for i in range(len(N)):
        for j in range(len(N)):
            if X[k,i,j].x == 1 :
                chauffeur.append((N[i],N[j],B[k,i].x))
                res += time[N[j]][N[i]]
    chauffeur.sort(key = takeThird)
    attrib.append((k,chauffeur))
    print("Le chauffeur {} effectue les courses suivantes : {}".format(k,chauffeur))
print("Temps total de trajet : {}".format(res)) # Affiche le temps total de trajet de tous les chauffeurs réunis



Attribution des courses :
Le chauffeur 1 effectue les courses suivantes : [('s0', 's23', 45000.0), ('s23', 's29', 46737.0), ('s29', 's17', 48416.0), ('s17', 's28', 49164.0), ('s28', 's14', 49431.0), ('s14', 's20', 50074.0), ('s20', 's17', 50769.0), ('s17', 's1', 51600.0), ('s1', 's0', 52231.0)]
Le chauffeur 2 effectue les courses suivantes : [('s0', 's21', 31836.0), ('s21', 's4', 38077.0), ('s4', 's0', 38631.0)]
Le chauffeur 3 effectue les courses suivantes : [('s0', 's26', 52708.0), ('s26', 's27', 53700.0), ('s27', 's20', 54504.0), ('s20', 's17', 58200.0), ('s17', 's30', 58961.0), ('s30', 's1', 61193.0), ('s1', 's0', 62189.0)]
Le chauffeur 4 effectue les courses suivantes : [('s0', 's7', 36600.0), ('s7', 's20', 37200.0), ('s20', 's10', 37834.0), ('s10', 's22', 42024.0), ('s22', 's10', 42626.0), ('s10', 's20', 44409.0), ('s20', 's7', 44821.0), ('s7', 's7', 45346.0), ('s7', 's16', 45406.0), ('s16', 's10', 46800.0), ('s10', 's0', 47394.0)]
Le chauffeur 5 effectue les courses suivantes : 

### Optimisation du second objectif

In [91]:
for i in range(1,len(N)//2): # somme sur les courses
    M.addLConstr(grb.quicksum([X[k,i,j] for k in range(1,m+1) for j in range(0,len(N))]), sense = "=", rhs = 1)

In [92]:
M.setObjective(quicksum([X[k,i,j]*time[N[j]][N[i]] for i in range(len(N)) for j in range(len(N)) for k in range(1,m+1)]),GRB.MINIMIZE)
M.update()
print(M.display())

Minimize
<gurobi.LinExpr: 842.0 X[1,0,1] + 1084.0 X[1,0,2] + 386.0 X[1,0,3] + 713.0 X[1,0,4]
+ 129.0 X[1,0,5] + 765.0 X[1,0,6] + 386.0 X[1,0,7] + 1092.0 X[1,0,8] + 129.0 X[1,0,9]
+ 386.0 X[1,0,10] + 992.0 X[1,0,11] + 842.0 X[1,0,12] + 713.0 X[1,0,13]
+ 493.0 X[1,0,14] + 713.0 X[1,0,15] + 740.0 X[1,0,16] + 667.0 X[1,0,17]
+ 740.0 X[1,0,18] + 1092.0 X[1,0,19] + 129.0 X[1,0,20] + 478.0 X[1,0,21]
+ 864.0 X[1,0,22] + 478.0 X[1,0,23] + 1132.0 X[1,0,24] + 842.0 X[1,0,25]
+ 251.0 X[1,0,26] + 439.0 X[1,0,27] + 478.0 X[1,0,28] + 251.0 X[1,0,29]
+ 713.0 X[1,0,30] + 332.0 X[1,0,31] + 783.0 X[1,0,32] + 493.0 X[1,0,33]
+ 851.0 X[1,0,34] + 842.0 X[1,0,35] + 354.0 X[1,0,36] + 386.0 X[1,0,37]
+ 251.0 X[1,0,38] + 1092.0 X[1,0,39] + 129.0 X[1,0,40] + 667.0 X[1,0,41]
+ 740.0 X[1,0,42] + 667.0 X[1,0,43] + 306.0 X[1,0,44] + 478.0 X[1,0,45]
+ 129.0 X[1,0,46] + 327.0 X[1,0,47] + 386.0 X[1,0,48] + 251.0 X[1,0,49]
+ 386.0 X[1,0,50] + 872.0 X[1,1,0] + 718.0 X[1,1,2] + 534.0 X[1,1,3] + 154.0 X[1,1,4]
+ 886.0 X[1,

+ 1143.0 X[1,9,24] + 830.0 X[1,9,25] + 269.0 X[1,9,26] + 419.0 X[1,9,27]
+ 465.0 X[1,9,28] + 269.0 X[1,9,29] + 701.0 X[1,9,30] + 319.0 X[1,9,31]
+ 816.0 X[1,9,32] + 483.0 X[1,9,33] + 904.0 X[1,9,34] + 830.0 X[1,9,35]
+ 250.0 X[1,9,36] + 340.0 X[1,9,37] + 269.0 X[1,9,38] + 1066.0 X[1,9,39]
+ 655.0 X[1,9,41] + 728.0 X[1,9,42] + 655.0 X[1,9,43] + 178.0 X[1,9,44]
+ 465.0 X[1,9,45] + 482.0 X[1,9,47] + 340.0 X[1,9,48] + 269.0 X[1,9,49]
+ 340.0 X[1,9,50] + 156.0 X[1,9,51] + 340.0 X[1,10,0] + 590.0 X[1,10,1]
+ 808.0 X[1,10,2] + 458.0 X[1,10,4] + 352.0 X[1,10,5] + 589.0 X[1,10,6]
+ 780.0 X[1,10,8] + 352.0 X[1,10,9] + 747.0 X[1,10,11] + 590.0 X[1,10,12]
+ 458.0 X[1,10,13] + 226.0 X[1,10,14] + 458.0 X[1,10,15] + 488.0 X[1,10,16]
+ 406.0 X[1,10,17] + 488.0 X[1,10,18] + 780.0 X[1,10,19] + 352.0 X[1,10,20]
+ 579.0 X[1,10,21] + 631.0 X[1,10,22] + 579.0 X[1,10,23] + 886.0 X[1,10,24]
+ 590.0 X[1,10,25] + 148.0 X[1,10,26] + 152.0 X[1,10,27] + 579.0 X[1,10,28]
+ 148.0 X[1,10,29] + 458.0 X[1,10,30] + 80.0

+ 1096.0 X[1,18,23] + 658.0 X[1,18,24] + 162.0 X[1,18,25] + 680.0 X[1,18,26]
+ 627.0 X[1,18,27] + 1096.0 X[1,18,28] + 680.0 X[1,18,29] + 180.0 X[1,18,30]
+ 457.0 X[1,18,31] + 169.0 X[1,18,32] + 516.0 X[1,18,33] + 1147.0 X[1,18,34]
+ 162.0 X[1,18,35] + 541.0 X[1,18,36] + 533.0 X[1,18,37] + 680.0 X[1,18,38]
+ 357.0 X[1,18,39] + 795.0 X[1,18,40] + 583.0 X[1,18,41] + 583.0 X[1,18,43]
+ 839.0 X[1,18,44] + 1096.0 X[1,18,45] + 795.0 X[1,18,46] + 843.0 X[1,18,47]
+ 533.0 X[1,18,48] + 680.0 X[1,18,49] + 533.0 X[1,18,50] + 866.0 X[1,18,51]
+ 1070.0 X[1,19,0] + 383.0 X[1,19,1] + 931.0 X[1,19,2] + 801.0 X[1,19,3]
+ 399.0 X[1,19,4] + 1125.0 X[1,19,5] + 1199.0 X[1,19,6] + 801.0 X[1,19,7]
+ 1125.0 X[1,19,9] + 801.0 X[1,19,10] + 901.0 X[1,19,11] + 383.0 X[1,19,12]
+ 399.0 X[1,19,13] + 832.0 X[1,19,14] + 399.0 X[1,19,15] + 437.0 X[1,19,16]
+ 961.0 X[1,19,17] + 437.0 X[1,19,18] + 1125.0 X[1,19,20] + 1315.0 X[1,19,21]
+ 599.0 X[1,19,22] + 1315.0 X[1,19,23] + 1018.0 X[1,19,24] + 383.0 X[1,19,25]
+ 949.0 X

+ 302.0 X[1,27,14] + 521.0 X[1,27,15] + 547.0 X[1,27,16] + 471.0 X[1,27,17]
+ 547.0 X[1,27,18] + 899.0 X[1,27,19] + 357.0 X[1,27,20] + 576.0 X[1,27,21]
+ 717.0 X[1,27,22] + 576.0 X[1,27,23] + 941.0 X[1,27,24] + 649.0 X[1,27,25]
+ 210.0 X[1,27,26] + 576.0 X[1,27,28] + 210.0 X[1,27,29] + 521.0 X[1,27,30]
+ 139.0 X[1,27,31] + 581.0 X[1,27,32] + 302.0 X[1,27,33] + 611.0 X[1,27,34]
+ 649.0 X[1,27,35] + 286.0 X[1,27,36] + 176.0 X[1,27,37] + 210.0 X[1,27,38]
+ 899.0 X[1,27,39] + 357.0 X[1,27,40] + 471.0 X[1,27,41] + 547.0 X[1,27,42]
+ 471.0 X[1,27,43] + 458.0 X[1,27,44] + 576.0 X[1,27,45] + 357.0 X[1,27,46]
+ 292.0 X[1,27,47] + 176.0 X[1,27,48] + 210.0 X[1,27,49] + 176.0 X[1,27,50]
+ 461.0 X[1,27,51] + 564.0 X[1,28,0] + 1158.0 X[1,28,1] + 1153.0 X[1,28,2]
+ 698.0 X[1,28,3] + 1052.0 X[1,28,4] + 574.0 X[1,28,5] + 731.0 X[1,28,6]
+ 698.0 X[1,28,7] + 1357.0 X[1,28,8] + 574.0 X[1,28,9] + 698.0 X[1,28,10]
+ 1113.0 X[1,28,11] + 1158.0 X[1,28,12] + 1052.0 X[1,28,13] + 795.0 X[1,28,14]
+ 1052.0 X[1,28

+ 255.0 X[1,36,5] + 668.0 X[1,36,6] + 170.0 X[1,36,7] + 822.0 X[1,36,8]
+ 255.0 X[1,36,9] + 170.0 X[1,36,10] + 808.0 X[1,36,11] + 634.0 X[1,36,12]
+ 513.0 X[1,36,13] + 319.0 X[1,36,14] + 513.0 X[1,36,15] + 563.0 X[1,36,16]
+ 491.0 X[1,36,17] + 563.0 X[1,36,18] + 822.0 X[1,36,19] + 255.0 X[1,36,20]
+ 719.0 X[1,36,21] + 730.0 X[1,36,22] + 719.0 X[1,36,23] + 971.0 X[1,36,24]
+ 634.0 X[1,36,25] + 196.0 X[1,36,26] + 299.0 X[1,36,27] + 719.0 X[1,36,28]
+ 196.0 X[1,36,29] + 513.0 X[1,36,30] + 156.0 X[1,36,31] + 692.0 X[1,36,32]
+ 319.0 X[1,36,33] + 844.0 X[1,36,34] + 634.0 X[1,36,35] + 170.0 X[1,36,37]
+ 196.0 X[1,36,38] + 822.0 X[1,36,39] + 255.0 X[1,36,40] + 491.0 X[1,36,41]
+ 563.0 X[1,36,42] + 491.0 X[1,36,43] + 303.0 X[1,36,44] + 719.0 X[1,36,45]
+ 255.0 X[1,36,46] + 530.0 X[1,36,47] + 170.0 X[1,36,48] + 196.0 X[1,36,49]
+ 170.0 X[1,36,50] + 355.0 X[1,36,51] + 340.0 X[1,37,0] + 590.0 X[1,37,1]
+ 808.0 X[1,37,2] + 458.0 X[1,37,4] + 352.0 X[1,37,5] + 589.0 X[1,37,6]
+ 780.0 X[1,37,8] + 352

...

'X[6,45,2]', 'X[6,45,3]', 'X[6,45,4]', 'X[6,45,5]', 'X[6,45,6]', 'X[6,45,7]',
'X[6,45,8]', 'X[6,45,9]', 'X[6,45,10]', 'X[6,45,11]', 'X[6,45,12]', 'X[6,45,13]',
'X[6,45,14]', 'X[6,45,15]', 'X[6,45,16]', 'X[6,45,17]', 'X[6,45,18]', 'X[6,45,19]',
'X[6,45,20]', 'X[6,45,21]', 'X[6,45,22]', 'X[6,45,23]', 'X[6,45,24]', 'X[6,45,25]',
'X[6,45,26]', 'X[6,45,27]', 'X[6,45,28]', 'X[6,45,29]', 'X[6,45,30]', 'X[6,45,31]',
'X[6,45,32]', 'X[6,45,33]', 'X[6,45,34]', 'X[6,45,35]', 'X[6,45,36]', 'X[6,45,37]',
'X[6,45,38]', 'X[6,45,39]', 'X[6,45,40]', 'X[6,45,41]', 'X[6,45,42]', 'X[6,45,43]',
'X[6,45,44]', 'X[6,45,45]', 'X[6,45,46]', 'X[6,45,47]', 'X[6,45,48]', 'X[6,45,49]',
'X[6,45,50]', 'X[6,45,51]', 'X[6,46,0]', 'X[6,46,1]', 'X[6,46,2]', 'X[6,46,3]',
'X[6,46,4]', 'X[6,46,5]', 'X[6,46,6]', 'X[6,46,7]', 'X[6,46,8]', 'X[6,46,9]',
'X[6,46,10]', 'X[6,46,11]', 'X[6,46,12]', 'X[6,46,13]', 'X[6,46,14]', 'X[6,46,15]',
'X[6,46,16]', 'X[6,46,17]', 'X[6,46,18]', 'X[6,46,19]', 'X[6,46,20]', 'X[6,46,21]',
'X[6,46,22

'X[7,4,46]', 'X[7,4,47]', 'X[7,4,48]', 'X[7,4,49]', 'X[7,4,50]', 'X[7,4,51]',
'X[7,5,0]', 'X[7,5,1]', 'X[7,5,2]', 'X[7,5,3]', 'X[7,5,4]', 'X[7,5,5]', 'X[7,5,6]',
'X[7,5,7]', 'X[7,5,8]', 'X[7,5,9]', 'X[7,5,10]', 'X[7,5,11]', 'X[7,5,12]', 'X[7,5,13]',
'X[7,5,14]', 'X[7,5,15]', 'X[7,5,16]', 'X[7,5,17]', 'X[7,5,18]', 'X[7,5,19]',
'X[7,5,20]', 'X[7,5,21]', 'X[7,5,22]', 'X[7,5,23]', 'X[7,5,24]', 'X[7,5,25]',
'X[7,5,26]', 'X[7,5,27]', 'X[7,5,28]', 'X[7,5,29]', 'X[7,5,30]', 'X[7,5,31]',
'X[7,5,32]', 'X[7,5,33]', 'X[7,5,34]', 'X[7,5,35]', 'X[7,5,36]', 'X[7,5,37]',
'X[7,5,38]', 'X[7,5,39]', 'X[7,5,40]', 'X[7,5,41]', 'X[7,5,42]', 'X[7,5,43]',
'X[7,5,44]', 'X[7,5,45]', 'X[7,5,46]', 'X[7,5,47]', 'X[7,5,48]', 'X[7,5,49]',
'X[7,5,50]', 'X[7,5,51]', 'X[7,6,0]', 'X[7,6,1]', 'X[7,6,2]', 'X[7,6,3]', 'X[7,6,4]',
'X[7,6,5]', 'X[7,6,6]', 'X[7,6,7]', 'X[7,6,8]', 'X[7,6,9]', 'X[7,6,10]', 'X[7,6,11]',
'X[7,6,12]', 'X[7,6,13]', 'X[7,6,14]', 'X[7,6,15]', 'X[7,6,16]', 'X[7,6,17]',
'X[7,6,18]', 'X[7,6,19]', 'X[7,6

'X[7,16,38]', 'X[7,16,39]', 'X[7,16,40]', 'X[7,16,41]', 'X[7,16,42]', 'X[7,16,43]',
'X[7,16,44]', 'X[7,16,45]', 'X[7,16,46]', 'X[7,16,47]', 'X[7,16,48]', 'X[7,16,49]',
'X[7,16,50]', 'X[7,16,51]', 'X[7,17,0]', 'X[7,17,1]', 'X[7,17,2]', 'X[7,17,3]',
'X[7,17,4]', 'X[7,17,5]', 'X[7,17,6]', 'X[7,17,7]', 'X[7,17,8]', 'X[7,17,9]',
'X[7,17,10]', 'X[7,17,11]', 'X[7,17,12]', 'X[7,17,13]', 'X[7,17,14]', 'X[7,17,15]',
'X[7,17,16]', 'X[7,17,17]', 'X[7,17,18]', 'X[7,17,19]', 'X[7,17,20]', 'X[7,17,21]',
'X[7,17,22]', 'X[7,17,23]', 'X[7,17,24]', 'X[7,17,25]', 'X[7,17,26]', 'X[7,17,27]',
'X[7,17,28]', 'X[7,17,29]', 'X[7,17,30]', 'X[7,17,31]', 'X[7,17,32]', 'X[7,17,33]',
'X[7,17,34]', 'X[7,17,35]', 'X[7,17,36]', 'X[7,17,37]', 'X[7,17,38]', 'X[7,17,39]',
'X[7,17,40]', 'X[7,17,41]', 'X[7,17,42]', 'X[7,17,43]', 'X[7,17,44]', 'X[7,17,45]',
'X[7,17,46]', 'X[7,17,47]', 'X[7,17,48]', 'X[7,17,49]', 'X[7,17,50]', 'X[7,17,51]',
'X[7,18,0]', 'X[7,18,1]', 'X[7,18,2]', 'X[7,18,3]', 'X[7,18,4]', 'X[7,18,5]',
'X[7,18,

'X[7,28,8]', 'X[7,28,9]', 'X[7,28,10]', 'X[7,28,11]', 'X[7,28,12]', 'X[7,28,13]',
'X[7,28,14]', 'X[7,28,15]', 'X[7,28,16]', 'X[7,28,17]', 'X[7,28,18]', 'X[7,28,19]',
'X[7,28,20]', 'X[7,28,21]', 'X[7,28,22]', 'X[7,28,23]', 'X[7,28,24]', 'X[7,28,25]',
'X[7,28,26]', 'X[7,28,27]', 'X[7,28,28]', 'X[7,28,29]', 'X[7,28,30]', 'X[7,28,31]',
'X[7,28,32]', 'X[7,28,33]', 'X[7,28,34]', 'X[7,28,35]', 'X[7,28,36]', 'X[7,28,37]',
'X[7,28,38]', 'X[7,28,39]', 'X[7,28,40]', 'X[7,28,41]', 'X[7,28,42]', 'X[7,28,43]',
'X[7,28,44]', 'X[7,28,45]', 'X[7,28,46]', 'X[7,28,47]', 'X[7,28,48]', 'X[7,28,49]',
'X[7,28,50]', 'X[7,28,51]', 'X[7,29,0]', 'X[7,29,1]', 'X[7,29,2]', 'X[7,29,3]',
'X[7,29,4]', 'X[7,29,5]', 'X[7,29,6]', 'X[7,29,7]', 'X[7,29,8]', 'X[7,29,9]',
'X[7,29,10]', 'X[7,29,11]', 'X[7,29,12]', 'X[7,29,13]', 'X[7,29,14]', 'X[7,29,15]',
'X[7,29,16]', 'X[7,29,17]', 'X[7,29,18]', 'X[7,29,19]', 'X[7,29,20]', 'X[7,29,21]',
'X[7,29,22]', 'X[7,29,23]', 'X[7,29,24]', 'X[7,29,25]', 'X[7,29,26]', 'X[7,29,27]',
'X[7

'X[7,39,30]', 'X[7,39,31]', 'X[7,39,32]', 'X[7,39,33]', 'X[7,39,34]', 'X[7,39,35]',
'X[7,39,36]', 'X[7,39,37]', 'X[7,39,38]', 'X[7,39,39]', 'X[7,39,40]', 'X[7,39,41]',
'X[7,39,42]', 'X[7,39,43]', 'X[7,39,44]', 'X[7,39,45]', 'X[7,39,46]', 'X[7,39,47]',
'X[7,39,48]', 'X[7,39,49]', 'X[7,39,50]', 'X[7,39,51]', 'X[7,40,0]', 'X[7,40,1]',
'X[7,40,2]', 'X[7,40,3]', 'X[7,40,4]', 'X[7,40,5]', 'X[7,40,6]', 'X[7,40,7]',
'X[7,40,8]', 'X[7,40,9]', 'X[7,40,10]', 'X[7,40,11]', 'X[7,40,12]', 'X[7,40,13]',
'X[7,40,14]', 'X[7,40,15]', 'X[7,40,16]', 'X[7,40,17]', 'X[7,40,18]', 'X[7,40,19]',
'X[7,40,20]', 'X[7,40,21]', 'X[7,40,22]', 'X[7,40,23]', 'X[7,40,24]', 'X[7,40,25]',
'X[7,40,26]', 'X[7,40,27]', 'X[7,40,28]', 'X[7,40,29]', 'X[7,40,30]', 'X[7,40,31]',
'X[7,40,32]', 'X[7,40,33]', 'X[7,40,34]', 'X[7,40,35]', 'X[7,40,36]', 'X[7,40,37]',
'X[7,40,38]', 'X[7,40,39]', 'X[7,40,40]', 'X[7,40,41]', 'X[7,40,42]', 'X[7,40,43]',
'X[7,40,44]', 'X[7,40,45]', 'X[7,40,46]', 'X[7,40,47]', 'X[7,40,48]', 'X[7,40,49]',
'X

In [93]:
M.optimize()

Presolve removed 36813 rows and 15280 columns
Presolve time: 4.22s
Presolved: 7909 rows, 7384 columns, 46864 nonzeros
Variable types: 0 continuous, 7384 integer (6663 binary)

Root relaxation: objective 1.680700e+04, 2146 iterations, 0.39 seconds (0.14 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 16835.0926    0  311 34078.0000 16835.0926  50.6%     -    4s
H    0     0                    33934.000000 16835.0926  50.4%     -    5s
     0     0 17683.1863    0  505 33934.0000 17683.1863  47.9%     -    6s
     0     0 17756.4055    0  519 33934.0000 17756.4055  47.7%     -    6s
     0     0 17757.0064    0  513 33934.0000 17757.0064  47.7%     -    6s
     0     0 18119.5238    0  532 33934.0000 18119.5238  46.6%     -    8s
     0     0 18338.1027    0  556 33934.0000 18338.1027  46.0%     -    9s
     0     0 18418.1064    0  628 33934.0000 18418.1064  4

 12102  7098 24092.6019   53  411 27007.0000 23394.6239  13.4%   226  230s
 12785  7446 25270.7445   73  382 27007.0000 23422.2002  13.3%   223  235s
 13275  7860 24453.7482   47  425 27007.0000 23453.3840  13.2%   222  240s
 13933  8271 26094.3515   79  263 27007.0000 23469.4017  13.1%   220  245s
 14591  8274 24641.7108   74  392 27007.0000 23491.0355  13.0%   219  250s
 14615  8290 25811.0775   86  663 27007.0000 23491.0355  13.0%   218  255s
 14641  8307 25783.2459   88  664 27007.0000 23491.0355  13.0%   218  260s
 14660  8320 24965.9246  105  654 27007.0000 23491.0355  13.0%   218  265s
 14690  8340 24798.2292   58  663 27007.0000 23491.0355  13.0%   217  270s
 14712  8355 24862.9909   64  632 27007.0000 23491.0355  13.0%   217  275s
 14717  8359 23491.0355   37  606 27007.0000 23491.0355  13.0%   219  280s
 14733  8356 23491.0355   41  567 27007.0000 23491.0355  13.0%   219  286s
 14805  8382 23491.0355   47  511 27007.0000 23491.0355  13.0%   220  290s
 15001  8462 23491.0355  

### Affichage de la solution finale

In [98]:
# Affichage de la solution
attrib = []
print("Attribution des courses :")
res = 0
for k in range(1,m+1):
    chauffeur = []
    for i in range(len(N)):
        for j in range(len(N)):
            if X[k,i,j].x == 1:
                chauffeur.append((N[i],N[j],B[k,i].x))
                res += time[N[j]][N[i]]
    chauffeur.sort(key = takeThird)
    attrib.append((k,chauffeur))
    print("Le chauffeur {} effectue les courses suivantes : {}".format(k,chauffeur))
print("Temps total de trajet : {}".format(res)) # Affiche le temps total de trajet de tous les chauffeurs réunis

Attribution des courses :
Le chauffeur 1 effectue les courses suivantes : [('s0', 's20', 45000.0), ('s20', 's7', 45129.0), ('s7', 's18', 45654.0), ('s18', 's17', 48900.0), ('s17', 's19', 49722.0), ('s19', 's20', 50317.0), ('s20', 's20', 50734.0), ('s20', 's25', 53700.0), ('s25', 's0', 54664.0)]
Le chauffeur 2 effectue les courses suivantes : [('s0', 's11', 31836.0), ('s11', 's8', 32700.0), ('s8', 's0', 33534.0)]
Le chauffeur 3 effectue les courses suivantes : [('s0', 's10', 53182.0), ('s10', 's14', 55716.0), ('s14', 's24', 56182.0), ('s24', 's16', 56620.0), ('s16', 's28', 57233.0), ('s28', 's23', 57434.0), ('s23', 's30', 58780.0), ('s30', 's1', 61193.0), ('s1', 's0', 62189.0)]
Le chauffeur 4 effectue les courses suivantes : [('s0', 's10', 36600.0), ('s10', 's7', 44158.0), ('s7', 's23', 44797.0), ('s23', 's16', 46325.0), ('s16', 's10', 46800.0), ('s10', 's29', 47774.0), ('s29', 's0', 48239.0)]
Le chauffeur 5 effectue les courses suivantes : [('s0', 's28', 48600.0), ('s28', 's28', 49340.

### Création du fichier JSON vérifiant la faisabilité de la solution

In [99]:
dict1 = {}
dict1["nb_assigned_bookings"]=25
dict1["route_cost"]=M.objVal
dict1["shifts"]= []
for k in range(1,m+1):
    dict1["shifts"].append({"id":chauffeurs[k-1]["id"],"jobs": []})
    for i in range(1,n+1):
        for j in range(1,len(N)-1):
            if X[k,i,j].x==1:
                dpu={"id":0, "time":0}
                ddo={"id":0, "time":0}
                dpu["id"]=courses[i-1]["jobs"][0]["id"]
                dpu["time"]=B[k,i].x
                ddo["id"]=courses[i-1]["jobs"][1]["id"]
                ddo["time"]=B[k,n+i].x
                dict1["shifts"][k-1]["jobs"].append(dpu)
                dict1["shifts"][k-1]["jobs"].append(ddo)

In [100]:
out_file = open("sortie.json","w")
json.dump(dict1, out_file)
out_file.close()